In [73]:
from fenics import *
from dolfin import *

import numpy as np
import matplotlib.pyplot as plt
import h5py

import pdb

class PeriodicBoundary(SubDomain):

    # Left boundary is "target domain" G
    def inside(self, x, on_boundary):
        # return bool(((x[0] < DOLFIN_EPS) or (x[0] > 1 + DOLFIN_EPS)) and on_boundary)
        return bool((x[0] < DOLFIN_EPS) or (x[0] > (1.0 + DOLFIN_EPS)))# and on_boundary)
        # return bool(- DOLFIN_EPS < x[0] < DOLFIN_EPS and on_boundary)

    # Map right boundary (H) to left boundary (G)
    def map(self, x, y):
        y[0] = x[0] - 1

# Create periodic boundary condition
x_res = 2048
t_res = 10 * x_res#int(1/(1 * (1/x_res)))
x_coordinate = np.linspace(0,1, x_res)
# t_coordinate = np.linspace(0,2, 2048)

t_coordinate = np.linspace(0,1, t_res)

for _nu_ in [1]:#np.logspace(-4, 0, 10):
    solution = np.zeros((30,t_res,x_res))
    # pdb.set_trace()
    Amp = [1, 1]
    k = [5 * 2 * np.pi, 3 * 2 * np.pi]
    phi = [np.pi/4, np.pi/6]
    # Create periodic boundary condition
    pbc = PeriodicBoundary()
    i = 0
    n = x_res - 1
    mesh = UnitIntervalMesh(n)
    V = FunctionSpace(mesh, "P", 1, constrained_domain=pbc)
    initial_cond = "{}*sin({}*x[0] + {}) + {}*sin({}*x[0] + {})".format(Amp[0], k[0], phi[0],Amp[1], k[1], phi[1])

    print("i: ", i, "initial_condition: ", initial_cond)
    # 
    # u0 = Constant(1)
    # bc = []
    u = interpolate(Expression((initial_cond,)[0], degree = 1),  V)


    u_next = TrialFunction(V)
    v = TestFunction(V)


    nu = Constant(_nu_)
    timestep = Constant(t_coordinate[1])
    F = ((((u_next - u ) * v) / timestep ) + ((nu * grad(u_next) * v))[0])* dx
    a, L = lhs(F), rhs(F)

    u_next = Function(V)
    M = u*dx
    t = t_coordinate[1]
    end = np.max(t_coordinate)
    j = 1
    solution[i,0,:] =  u.compute_vertex_values()
    while t <= end:
        # solve(F == 0, u_next, bc)

        # solve(a == L, u_next, [],
        #       tol = 1e-9, 
        #       M=M)
        #       solver_parameters={'linear_solver': 'gmres',
        #                                             'preconditioner': 'ilu'})
        #                                             "relative_tolerance":1e-1,
                                                    # "absolute_tolerance":1e-1})

        problem = LinearVariationalProblem(a, L, u_next, [])
        solver = AdaptiveLinearVariationalSolver(problem, goal= M)
        # solver.parameters['linear_solver'] = 'gmres'
        # solver.parameters['preconditioner'] = 'ilu'
        # prm = solver.parameters.krylov_solver  # short form
        # solver.parameters['krylov_solver']['absolute_tolerance'] = 1E-6
        # solver.parameters['krylov_solver']['relative_tolerance'] = 1E-6
        solver.solve(tol = 1e-6)

        u.assign(u_next)
        t += float(timestep)
        solution[i,j,:] = u.compute_vertex_values()
        j += 1

    f = h5py.File('/home/divyam123/fenics/advection/1D_Advection_Sols_Beta{}.hdf5'.format(_nu_), 'w')
    f['x-coordinate'] = x_coordinate
    f['t-coordinate'] = t_coordinate
    f['tensor'] = solution
    f.close()



i:  0 initial_condition:  1*sin(31.41592653589793*x[0] + 0.7853981633974483) + 1*sin(18.84955592153876*x[0] + 0.5235987755982988)
1 4.883050930221202e-05
Generating forms required for error control, this may take some time...
Solving variational problem adaptively
Adaptive iteration 0
  Solving linear variational problem.
  Value of goal functional is -2.14564e-16.
  Solving linear variational problem.
Error estimate (0) is less than tolerance (1e-06), returning.
2 9.766101860442404e-05
Generating forms required for error control, this may take some time...
Solving variational problem adaptively
3 0.00014649152790663605
Adaptive iteration 0
  Solving linear variational problem.
  Value of goal functional is -2.05998e-17.
  Solving linear variational problem.
Error estimate (0) is less than tolerance (1e-06), returning.
Generating forms required for error control, this may take some time...
Solving variational problem adaptively
4 0.0001953220372088481
Adaptive iteration 0
  Solving lin

In [48]:
_nu_

0.005994842503189409

In [1]:
from fenics import *
from dolfin import *

import numpy as np
import matplotlib.pyplot as plt
import h5py

import pdb




In [60]:
class PeriodicBoundary(SubDomain):

    # Left boundary is "target domain" G
    def inside(self, x, on_boundary):
        # return bool(((x[0] < DOLFIN_EPS) or (x[0] > 1 + DOLFIN_EPS)) and on_boundary)
        return bool((x[0] < DOLFIN_EPS) or (x[0] > (1.0 + DOLFIN_EPS)))# and on_boundary)
        # return bool(- DOLFIN_EPS < x[0] < DOLFIN_EPS and on_boundary)

    # Map right boundary (H) to left boundary (G)
    def map(self, x, y):
        y[0] = x[0] - 1

x_res = 2048
t_res = 10 * x_res #int(1/(1 * (1/x_res)))
x_coordinate = np.linspace(0,1, x_res)
# t_coordinate = np.linspace(0,2, 2048)

t_coordinate = np.linspace(0,1, t_res)
_nu_ = 0.001
solution = np.zeros((30,t_res,x_res))
# pdb.set_trace()
Amp = [1, 1]
k = [5 * 2 * np.pi, 3 * 2 * np.pi]
phi = [np.pi/4, np.pi/6]
# Create periodic boundary condition
pbc = PeriodicBoundary()
i = 0
n = x_res - 1
mesh = UnitIntervalMesh(n)
V = FunctionSpace(mesh, "P", 1, constrained_domain=pbc)
initial_cond = "{}*sin({}*x[0] + {}) + {}*sin({}*x[0] + {})".format(Amp[0], k[0], phi[0],Amp[1], k[1], phi[1])

print("i: ", i, "initial_condition: ", initial_cond)
# 
# u0 = Constant(1)
# bc = []
u = interpolate(Expression((initial_cond,)[0], degree = 1),  V)


u_next = TrialFunction(V)
v = TestFunction(V)


nu = Constant(_nu_)
timestep = Constant(t_coordinate[1])
F = ((((u_next - u ) * v) / timestep ) + ((nu * grad(u_next) * v))[0])* dx
a, L = lhs(F), rhs(F)

u_next = Function(V)

t = t_coordinate[1]
end = np.max(t_coordinate)
j = 1
solution[i,0,:] =  u.compute_vertex_values()

i:  0 initial_condition:  1*sin(31.41592653589793*x[0] + 0.7853981633974483) + 1*sin(18.84955592153876*x[0] + 0.5235987755982988)


In [14]:
problem = LinearVariationalProblem(a, L, u_next, [])

In [45]:
problem = LinearVariationalProblem(a, L, u_next, [])
solver = LinearVariationalSolver(problem)
solver.parameters['krylov_solver']['absolute_tolerance'] = 1e-6
solver.parameters['krylov_solver']['relative_tolerance'] = 1e-6
# solver.solve()

In [46]:
solver.parameters.to_dict()

{'krylov_solver': {'absolute_tolerance': <dolfin.cpp.parameter.Parameter at 0x7f802ac156f0>,
  'divergence_limit': <dolfin.cpp.parameter.Parameter at 0x7f802ac174b0>,
  'error_on_nonconvergence': <dolfin.cpp.parameter.Parameter at 0x7f802ac143b0>,
  'maximum_iterations': <dolfin.cpp.parameter.Parameter at 0x7f802ac16870>,
  'monitor_convergence': <dolfin.cpp.parameter.Parameter at 0x7f802ac14470>,
  'nonzero_initial_guess': <dolfin.cpp.parameter.Parameter at 0x7f802ac14130>,
  'relative_tolerance': <dolfin.cpp.parameter.Parameter at 0x7f802ac17b30>,
  'report': <dolfin.cpp.parameter.Parameter at 0x7f802ac16cf0>},
 'linear_solver': <dolfin.cpp.parameter.Parameter at 0x7f802b477bb0>,
 'lu_solver': {'report': <dolfin.cpp.parameter.Parameter at 0x7f802b477330>,
  'symmetric': <dolfin.cpp.parameter.Parameter at 0x7f802b474fb0>,
  'verbose': <dolfin.cpp.parameter.Parameter at 0x7f802b476e30>},
 'preconditioner': <dolfin.cpp.parameter.Parameter at 0x7f802b476070>,
 'print_matrix': <dolfin.cpp

In [29]:

solver.parameters['krylov_solver']['absolute_tolerance'] = 1e-6
solver.parameters['krylov_solver']['relative_tolerance'] = 1e-6

In [30]:
solver.solve()

Solving linear variational problem.


In [31]:
solver.parameters['krylov_solver']['absolute_tolerance']

1e-06

In [61]:
t_res

20480